# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [A2C]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from stable_baselines3 import A2C #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.21.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.21.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.21.0\n')
wandb, version 0.13.3


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 65% average battery) 
#case = 'wohnblock_household_simulation_adaptive_18.yaml' #(18 EVs arrivals per week with 40% average battery) 
#case = 'wohnblock_household_simulation_adaptive_22.yaml' #(22 EVs arrivals per week with 55% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f2ac45045d0>Mean parking time: 23.9
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.9, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energy

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21774.14 , over-consume=kWh  39070.77 , under-consume=kWh  17296.63 , Total_cost=€  902.83 , overcost=€  1399.09 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/A2C_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/A2C_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="A2C_VPP_simulator.ipynb"


In [ ]:
#Loading training model, from local directory or from wandb previous trainings
A2C_path = "trained_models/A2C_models/model_A2C_"

model_id = "1u6pwi97"
model = A2C.load(A2C_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22499.74 , over-consume=kWh  39064.9 , under-consume=kWh  16565.16 , Total_cost=€  935.69 , overcost=€  1406.76 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6320.99 , over-consume=KWh  6757.38 , under-consume=KWh  13078.36 , Total_cost=€  -88.72 , Overcost=€  249.43 
 EV_INFO: Av.EV_energy_leaving=kWh  64.32 , Std.EV_energy_leaving=kWh  33.86 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 153080.88 - Step_rewars (load_t= 187854.11, EVs_energy_t= -30917.52)
 - Final_rewards (EVs_energy= 12828.16, Overconsume= -6244.01, Underconsume= -11053.32, Overcost= 613.45)
Episode:1 Score:153080.8772647144


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000  54.609520  68.958916  61.896244   
2022-01-01 00:15:00   0.000000  54.116833  68.466232  62.146244   
2022-01-01 00:30:00   0.000000  53.862980  68.212379  62.396244   
2022-01-01 00:45:00   0.000000  53.549652  67.899055  62.646244   
2022-01-01 01:00:00   0.000000  53.244576  67.593979  62.896244   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  66.581215  28.071095  34.898060  99.989998   
2022-06-06 05:00:00  68.253998  27.821095  34.648060  99.989998   
2022-06-06 05:15:00  70.068596  27.571095  34.398060  99.989998   
2022-06-06 05:30:00  71.868095  27.321095  34.148060  99.989998   
2022-06-06 05:45:00  73.539635  27.071095  33.898060  99.989998   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 2, 2, 1]   
2022-01-01 00:15:00     [0, 3128, 3129, 3127]  [2, 2, 2, 1]   
2022-01-01 00:30:00     [0, 3128, 3129, 3127]  [2, 2, 2, 1]   
2022-01-01 00:45:00     [0, 3128, 3129, 3127]  [2, 2, 2, 1]   
2022-01-01 01:00:00     [0, 3128, 3129, 3127]  [2, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [3576, 3574, 3575, 3573]  [1, 2, 2, 1]   
2022-06-06 05:00:00  [3576, 3574, 3575, 3573]  [1, 2, 2, 1]   
2022-06-06 05:15:00  [3576, 3574, 3575, 3573]  [1, 2, 2, 1]   
2022-06-06 05:30:00  [3576, 3574, 3575, 3573]  [1, 2, 2, 1]   
2022-06-06 05:45:00  [3576, 3574, 3575, 3573]  [1, 2, 2, 1]   

                                       mask_truth      load  load_reward  \
time                                                                       
2022-01-01 00:00:00  [False, False, False, False]  2.551364    15.000000   
2022-01-01 00:15:00    [False, True, True, False]  0.000000    15.000000   
2022-01-01 00:30:00    [False, True, True, False]  0.000000    15.000000   
2022-01-01 00:45:00    [False, True, True, False]  0.000000    15.000000   
2022-01-01 01:00:00    [False, True, True, False]  0.000000    15.000000   
...                                           ...       ...          ...   
2022-06-06 04:45:00   [True, False, False, False] -5.237641    -7.446486   
2022-06-06 05:00:00   [True, False, False, False] -6.691134    -7.962162   
2022-06-06 05:15:00   [True, False, False, False] -7.258378    -7.907274   
2022-06-06 05:30:00   [True, False, False, False] -7.198002    -7.441955   
2022-06-06 05:45:00   [True, False, False, False] -6.686151    -7.858478   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -7.446486  
2022-06-06 05:00:00        0.0  -7.962162  
2022-06-06 05:15:00        0.0  -7.907274  
2022-06-06 05:30:00        0.0  -7.441955  
2022-06-06 05:45:00        0.0  -7.858478  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 01:15:00, Parking_time: 24, Leaving_time: 2022-01-02 01:15:00, SOC: 0.5036726480294922, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-30 15:45:00, Parking_time: 24, Leaving_time: 2022-12-31 15:45:00, SOC: 0.20044102335573977, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12710.69 , over-consume=kWh  34609.94 , under-consume=kWh  21899.25 , Total_cost=€  600.81 , overcost=€  1494.38 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = A2C.load(A2C_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13335.33 , over-consume=kWh  34540.14 , under-consume=kWh  21204.81 , Total_cost=€  650.13 , overcost=€  1510.38 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -13123.65 , over-consume=KWh  3343.37 , under-consume=KWh  16467.01 , Total_cost=€  -498.91 , Overcost=€  146.31 
 EV_INFO: Av.EV_energy_leaving=kWh  66.26 , Std.EV_energy_leaving=kWh  33.49 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 164604.57 - Step_rewars (load_t= 194158.96, EVs_energy_t= -28251.11)
 - Final_rewards (EVs_energy= 11047.7, Overconsume= -3134.55, Underconsume= -10810.68, Overcost= 1594.25)
Episode:1 Score:164604.56934441536


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  80.555161  44.210461  48.379368  85.457169   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  67.941360  23.219040  34.049763  88.745102   
2022-06-06 05:00:00  69.995621  22.969040  33.799763  90.799362   
2022-06-06 05:15:00  72.061546  22.719040  33.549763  92.865288   
2022-06-06 05:30:00  73.947632  22.469040  33.299763  94.751373   
2022-06-06 05:45:00  75.893356  22.219040  33.049763  96.697098   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [1, 1, 0, 2]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [0, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [7730, 7727, 7728, 7729]  [1, 2, 2, 1]   
2022-06-06 05:00:00  [7730, 7727, 7728, 7729]  [1, 2, 2, 1]   
2022-06-06 05:15:00  [7730, 7727, 7728, 7729]  [1, 2, 2, 1]   
2022-06-06 05:30:00  [7730, 7727, 7728, 7729]  [1, 2, 2, 1]   
2022-06-06 05:45:00  [7730, 7727, 7728, 7729]  [1, 2, 2, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False] -4.174535e+00    15.000000   
2022-01-01 00:15:00   [False, False, True, False]  0.000000e+00    -3.612978   
2022-01-01 00:30:00     [True, True, False, True] -3.167787e+00    -4.053903   
2022-01-01 00:45:00     [True, True, False, True] -3.432342e+00    -5.269037   
2022-01-01 01:00:00     [True, True, False, True] -4.295941e+00    -4.985290   
...                                           ...           ...          ...   
2022-06-06 04:45:00    [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 05:00:00    [True, False, False, True] -1.776357e-15    15.000000   
2022-06-06 05:15:00   [True, False, False, False]  0.000000e+00    15.000000   
2022-06-06 05:30:00   [True, False, False, False]  0.000000e+00    15.000000   
2022-06-06 05:45:00   [True, False, False, False]  0.000000e+00    15.000000   

                      EV_reward     rewards  
time                                         
2022-01-01 00:00:00  120.255456  135.255456  
2022-01-01 00:15:00    0.000000   -3.612978  
2022-01-01 00:30:00    0.000000   -4.053903  
2022-01-01 00:45:00    0.000000   -5.269037  
2022-01-01 01:00:00    0.000000   -4.985290  
...                         ...         ...  
2022-06-06 04:45:00    0.000000   15.000000  
2022-06-06 05:00:00    0.000000   15.000000  
2022-06-06 05:15:00    0.000000   15.000000  
2022-06-06 05:30:00    0.000000   15.000000  
2022-06-06 05:45:00    0.000000   15.000000  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 8345, Arrival time: 2022-01-01 08:15:00, Parking_time: 24, Leaving_time: 2022-01-02 08:15:00, SOC: 0.356026238451636, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 9387, Arrival time: 2022-12-31 23:30:00, Parking_time: 23.747260653646272, Leaving_time: 2023-01-01 23:14:50.138353, SOC: 0.5765531482560226, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8550.54 , over-consume=kWh  31947.46 , under-consume=kWh  23396.93 , Total_cost=€  506.15 , overcost=€  1355.97 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = A2C.load(A2C_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9083.9 , over-consume=kWh  32908.94 , under-consume=kWh  23825.03 , Total_cost=€  495.82 , overcost=€  1367.63 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -16166.4 , over-consume=KWh  2836.1 , under-consume=KWh  19002.5 , Total_cost=€  -551.83 , Overcost=€  124.77 
 EV_INFO: Av.EV_energy_leaving=kWh  67.01 , Std.EV_energy_leaving=kWh  33.46 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 153302.88 - Step_rewars (load_t= 180069.77, EVs_energy_t= -25421.23)
 - Final_rewards (EVs_energy= 9894.6, Overconsume= -2701.23, Underconsume= -11204.73, Overcost= 2665.69)
Episode:1 Score:153302.87781402457


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  41.524815  68.142311  24.201294  80.720497   
2022-06-06 03:45:00  42.249084  67.892311  23.951294  81.444771   
2022-06-06 04:00:00  43.200123  67.642311  23.701294  82.395805   
2022-06-06 04:15:00  44.309921  67.392311  23.451294  83.505600   
2022-06-06 04:30:00  45.391914  67.142311  23.201294  84.587593   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [0, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [10873, 10871, 10870, 10872]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [10873, 10871, 10870, 10872]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [10873, 10871, 10870, 10872]  [1, 2, 2, 1]   
2022-06-06 04:15:00  [10873, 10871, 10870, 10872]  [1, 2, 2, 1]   
2022-06-06 04:30:00  [10873, 10871, 10870, 10872]  [1, 2, 2, 1]   

                                     mask_truth          load  load_reward  \
time                                                                         
2022-01-01 00:00:00   [True, True, False, True] -3.803376e+00    -3.300042   
2022-01-01 00:15:00   [True, True, False, True] -2.980025e+00    -4.345874   
2022-01-01 00:30:00   [True, True, False, True] -3.607524e+00    -3.000720   
2022-01-01 00:45:00   [True, True, False, True] -2.800432e+00    -6.099177   
2022-01-01 01:00:00   [True, True, False, True] -5.209095e+00    -5.842684   
...                                         ...           ...          ...   
2022-06-06 03:30:00  [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 03:45:00  [True, False, False, True]  4.440892e-16    15.000000   
2022-06-06 04:00:00  [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 04:15:00  [True, False, False, True]  8.881784e-16    15.000000   
2022-06-06 04:30:00  [True, False, False, True]  8.881784e-16    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -3.300042  
2022-01-01 00:15:00        0.0  -4.345874  
2022-01-01 00:30:00        0.0  -3.000720  
2022-01-01 00:45:00        0.0  -6.099177  
2022-01-01 01:00:00        0.0  -5.842684  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()